In [1]:
 !nvidia-smi

Sun Aug 21 09:11:20 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   48C    P8    10W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
!pip install simpletransformers -q

     |████████████████████████████████| 249 kB 6.9 MB/s 
     |████████████████████████████████| 365 kB 58.5 MB/s 
     |████████████████████████████████| 4.7 MB 57.3 MB/s 
     |████████████████████████████████| 1.3 MB 66.8 MB/s 
     |████████████████████████████████| 9.1 MB 48.2 MB/s 
     |████████████████████████████████| 43 kB 523 kB/s 
     |████████████████████████████████| 1.8 MB 58.2 MB/s 
     |████████████████████████████████| 6.6 MB 56.3 MB/s 
     |████████████████████████████████| 101 kB 12.4 MB/s 
     |████████████████████████████████| 157 kB 53.2 MB/s 
     |████████████████████████████████| 181 kB 57.4 MB/s 
     |████████████████████████████████| 63 kB 717 kB/s 
     |████████████████████████████████| 157 kB 75.6 MB/s 
     |████████████████████████████████| 157 kB 76.4 MB/s 
     |████████████████████████████████| 157 kB 78.7 MB/s 
     |████████████████████████████████| 157 kB 50.2 MB/s 
     |████████████████████████████████| 156 kB 65.7 MB/s 
     |█████████████

In [3]:
!pip install wandb -q

## wandb setup for visualization

In [4]:
import wandb

wandb.login()

<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [5]:
%env WANDB_ENTITY=afschowdhury
%env WANDB_PROJECT=HF_QAS_TEST


env: WANDB_ENTITY=afschowdhury
env: WANDB_PROJECT=HF_QAS_TEST


## Downloading Dataset From Kaggle

In [6]:
!pip install opendatasets --upgrade --quiet

In [7]:
!wget https://raw.githubusercontent.com/afs-chowdhury/afschowdhury/master/kaggle.json

--2022-08-21 09:12:04--  https://raw.githubusercontent.com/afs-chowdhury/afschowdhury/master/kaggle.json
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 73 [text/plain]
Saving to: ‘kaggle.json’

kaggle.json         100%[===================>]      73  --.-KB/s    in 0s      

2022-08-21 09:12:04 (3.47 MB/s) - ‘kaggle.json’ saved [73/73]



In [8]:
import opendatasets as od

dataset_url = 'https://www.kaggle.com/datasets/mayeesha/bengali-question-answering-dataset'

od.download(dataset_url)

100%|██████████| 19.1M/19.1M [00:00<00:00, 94.3MB/s]


## Exploring the data

In [9]:
import json
import pandas as pd

f = open('./bengali-question-answering-dataset/valid_bangla_samples_fixed_preprocessed.json')
valid_data = json.load(f)


In [10]:
with open(r"./bengali-question-answering-dataset/valid_bangla_samples_fixed_preprocessed.json", "r") as read_file:
    valid_data = json.load(read_file)

In [11]:
with open(r"./bengali-question-answering-dataset/train_bangla_samples_fixed_preprocessed.json", "r") as read_file:
    train_data = json.load(read_file)

In [12]:
valid_data

{'data': [{'title': 'Charleston,_South_Carolina',
   'paragraphs': [{'context': 'চার্লসটন আমেরিকা যুক্তরাষ্ট্রের দক্ষিণ ক্যারোলাইনা রাজ্যের প্রাচীনতম এবং দ্বিতীয় বৃহত্তম শহর, চার্লসটন কাউন্টির কাউন্টি আসন এবং চার্লসটন – নর্থ চার্লসটন – সামারভিলে মেট্রোপলিটন স্ট্যাটিস্টিকাল এরিয়ার প্রধান শহর  শহরটি দক্ষিণ ক্যারোলিনার উপকূলরেখার ভৌগলিক মিডপয়েন্টের ঠিক দক্ষিণে অবস্থিত এবং অ্যাশলে এবং কুপার নদীর নদীর সংগম দ্বারা গঠিত আটলান্টিক মহাসাগরের একটি খাঁটি চার্লস্টন হারবারে অবস্থিত, অথবা স্থানীয়ভাবে প্রকাশিত হয়েছে, "যেখানে কুপার এবং অ্যাশলে রয়েছে। নদীগুলি একত্র হয়ে আটলান্টিক মহাসাগর গঠনে আসে। "  ',
     'qas': [{'question': 'দক্ষিণ ক্যারোলিনার প্রাচীনতম শহরটি কী?  ',
       'id': '572e8700cb0c0d14000f1252',
       'is_impossible': True,
       'answers': []},
      {'question': 'চার্লসটন, দক্ষিণ ক্যারোলিনা কোন কাউন্টিতে অবস্থিত?  ',
       'id': '572e8700cb0c0d14000f1253',
       'is_impossible': False,
       'answers': [{'text': 'চার্লসটন আমেরিকা য', 'answer_start': 0}]},
      {'question'

In [13]:
len(valid_data['data'])

61

In [14]:
len(train_data["data"])

241

In [15]:
import logging

from simpletransformers.question_answering import QuestionAnsweringModel

In [16]:
model_type = "xlmroberta"
model_name = "xlm-roberta-base"

In [17]:
### Training args
train_args = {
    "reprocess_input_data": True,
    "overwrite_output_dir": True,
    "use_cached_eval_features": True,
    "output_dir": f"outputs/{model_type}",
    "best_model_dir": f"outputs/{model_type}/best_model",
    # "evaluate_during_training": True,
    "max_seq_length": 128,
    "num_train_epochs": 20,
    # "evaluate_during_training_steps": 1000,
    "wandb_project": "Question Answer Application",
    "wandb_kwargs": {"name": model_name},
    "save_model_every_epoch": False,
    "save_eval_checkpoints": False,
    "n_best_size":3,
    # "use_early_stopping": True,
    # "early_stopping_metric": "mcc",
    # "n_gpu": 2,
    # "manual_seed": 4,
    # "use_multiprocessing": False,
    "train_batch_size": 8,
    # "eval_batch_size": 64,
    # "config": {
    #     "output_hidden_states": True
    # }
}

In [18]:
model = QuestionAnsweringModel(
    model_type,model_name, args=train_args
)

Some weights of the model checkpoint at xlm-roberta-base were not used when initializing XLMRobertaForQuestionAnswering: ['lm_head.bias', 'lm_head.layer_norm.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.dense.weight']
- This IS expected if you are initializing XLMRobertaForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLMRobertaForQuestionAnswering were not initialized from the model checkpoint at xlm-roberta-base and are newly initialized: ['qa_outputs.weight', 'qa_outputs.bias']
You should probably TRAIN this model on a down-stream tas

In [19]:
train_data['data'][0]['paragraphs'][0]


{'context': 'রোমান প্রজাতন্ত্র লাতিন: রেজ পাবলিকা রোমানা; ধ্রুপদী লাতিন: ːː ˈː.ɪ. ːˈː. ছিল প্রাচীন রোমান সভ্যতার সময়কাল যা রোমান রাজ্যের উত্থানের মধ্য দিয়ে শুরু হয়েছিল, তিহ্যগতভাবে খ্রিস্টপূর্ব ৫০৯ অবধি, এবং শেষ হয়েছিল  খ্রিস্টপূর্ব ২ ২৭ রোমান সাম্রাজ্য প্রতিষ্ঠার সাথে। এই সময়কালেই রোমের নিয়ন্ত্রণ শহরের তাত্ক্ষণিক আশেপাশের অঞ্চল থেকে সমগ্র ভূমধ্যসাগরীয় অঞ্চলে আধিপত্য বিস্তার করে। এর অস্তিত্বের প্রথম দুটি শতাব্দীতে রোমান প্রজাতন্ত্রের বিজয় এবং জোটের সংমিশ্রণের মধ্য দিয়ে মধ্য ইতালি থেকে পুরো ইতালীয় উপদ্বীপে প্রসারিত হয়েছিল। পরবর্তী শতাব্দীর মধ্যে এটি উত্তর আফ্রিকা, স্পেন এবং বর্তমানে দক্ষিণ ফ্রান্স যা অন্তর্ভুক্ত করেছিল। এর দুই শতাব্দী পরে, খ্রিস্টপূর্ব প্রথম শতাব্দীর শেষের দিকে, এর মধ্যে আধুনিক ফ্রান্স, গ্রিস এবং পূর্ব ভূমধ্যসাগরীয় অংশের বেশিরভাগ অংশ অন্তর্ভুক্ত ছিল। এই সময়ের মধ্যে, অভ্যন্তরীণ উত্তেজনা একের পর এক গৃহযুদ্ধের দিকে পরিচালিত করেছিল, যার পরিণতি জুলিয়াস সিজারের হত্যার সাথে ঘটেছিল, যা প্রজাতন্ত্র থেকে সাম্রাজ্যের দিকে উত্তরণের দিকে পরিচালিত করেছিল। পরিবর্তনের সঠি

In [20]:
model.train_model(train_data['data'][0]['paragraphs'])

add example index and unique id: 100%|██████████| 386/386 [00:00<00:00, 759737.84it/s]
/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


Epoch:   0%|          | 0/20 [00:00<?, ?it/s]

wandb: Currently logged in as: afschowdhury. Use `wandb login --relogin` to force relogin


Running Epoch 0 of 20:   0%|          | 0/52 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/optim/lr_scheduler.py:136: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  "https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate", UserWarning)


...

Running Epoch 16 of 20:   0%|          | 0/52 [00:00<?, ?it/s]

Running Epoch 17 of 20:   0%|          | 0/52 [00:00<?, ?it/s]

Running Epoch 18 of 20:   0%|          | 0/52 [00:00<?, ?it/s]

Running Epoch 19 of 20:   0%|          | 0/52 [00:00<?, ?it/s]

(1040, 1.2434588487331684)

In [21]:
!nvidia-smi 

Sun Aug 21 09:16:25 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   73C    P0    34W /  70W |   7610MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------